In [ ]:
import dask.dataframe as dd
from dask.diagnostics import ProgressBar
import os

directory_path = '/Users/fionachow/Documents/NYU/CDS/Fall 2023/CSCI - GA 2271 - Computer Vision/Project/'

file_prefix = 'part'

def list_files_with_prefix(directory, prefix):
    file_paths = []

    for root, _, files in os.walk(directory):
        for file in files:
            if file.startswith(prefix):
                absolute_path = os.path.join(root, file)
                file_paths.append(absolute_path)

    return file_paths

laion_file_paths = list_files_with_prefix(directory_path, file_prefix)

dataframes = [dd.read_parquet(file) for file in laion_file_paths]
combined_dataframe = dd.multi.concat(dataframes)

with ProgressBar():
    row_count = combined_dataframe.shape[0].compute()
    print(row_count)

filtered_df = combined_dataframe[combined_dataframe['NSFW'] == "UNLIKELY"]

num_samples = 225_000
selected_rows = filtered_df.sample(frac=num_samples / filtered_df.shape[0].compute())

with ProgressBar():
    sampled_rows = selected_rows.compute()

print(len(sampled_rows))

with ProgressBar():
    selected_rows.to_parquet('laion_sampled', write_index=False)
